In [ ]:
from pyspark.sql import *

In [ ]:
%run "/Workspace/Users/cronies-02gorilla@icloud.com/post_batch_clean"

In [ ]:
%run "/Workspace/Users/cronies-02gorilla@icloud.com/geolocation_batch_clean"

In [ ]:
%run "/Workspace/Users/cronies-02gorilla@icloud.com/user_batch_clean"

In [ ]:
# join pinterest dataframes

# alias the dataframes to avoid column name ambiguity
pin_df_alias = pin_df.alias("pin")
geo_df_alias = geo_df.alias("geo")
user_df_alias = user_df.alias("user")

# perform the joins using the aliased dataframes
join_df = pin_df_alias.join(geo_df_alias, pin_df_alias["ind"] == geo_df_alias["ind"], how="inner")

# base_df is the final dataframe we will use
base_df = join_df.join(user_df_alias, join_df["pin.ind"] == user_df_alias["ind"], how="inner")

base_df = base_df.cache()

In [ ]:
# base_df manangement

# add post_year column
base_df = base_df.withColumn("post_year", year("timestamp"))

# add age_group column
base_df = base_df.withColumn("age_group", when(col("age") < 25, "18-24").when((col("age") >= 25) & (col("age") < 36), "25-35").when((col("age") >= 36) & (col("age") < 51), "36-50").otherwise("50+"))

# cache for performance
base_df = base_df.cache()

In [ ]:
display(base_df)

ind unique_id title description follower_count poster_name tag_list is_image_or_video image_src save_location category ind country coordinates timestamp ind user_name age date_joined post_year age_group 2581 75d7abff-5211-4052-969d-cea35e7b4e61 DIY Personalized Christmas Ornament Keepsakes That Kids Can Make (And You’ll Treasure Forever) Best list of kid-made Christmas ornaments that make great gifts & keepsakes. Crafts include salt dough handprints, photos, names, drawings & more! 105000 What Moms Love Christmas Handprint Crafts,Baby's 1st Christmas Ornament,Personalized Christmas Ornaments,Preschool Christmas,Christmas Gifts For Kids,Christmas Diy,Holiday Ornaments,Homemade Christmas Ornaments,Diy Christmas Ornaments For Toddlers image https://i.pinimg.com/originals/7f/5c/88/7f5c8896ba9ce9931cf1d55724953f09.png /data/christmas christmas 2581 Gabon List(-85.4432, -126.358) 2020-02-07T15:00:57.000+0000 2581 Brandon Smith 22 2016-08-27T13:05:47.000+0000 2020 18-24 1704 5fbf9863-fb79-477c-a5b6-540c3020a55f Christmas Trees From Pallet Wood | Holiday DIY Christmas Trees From Pallet Wood | Holiday DIY: Deck the yard with some fun outdoor Christmas Trees! We made these merry and bright decorations from two old pallets we had lying…  3000000 Instructables Pallet Wood Christmas Tree,Wooden Christmas Crafts,Diy Christmas Tree,Christmas Projects,Holiday Crafts,Wooden Xmas Trees,Different Christmas Trees,Pallet Tree,Christmas Kitchen image https://i.pinimg.com/originals/64/7b/ca/647bca35169b7c144604116c64bcba8a.png /data/christmas christmas 1704 Christmas Island List(-56.8702, -93.6232) 2018-11-29T04:46:39.000+0000 1704 Barry Lynn 20 2015-10-28T05:00:33.000+0000 2018 18-24 8880 c3567cb9-197c-4719-8223-4e64ba32fcbc 37 Examples of the Hypercolor Realism Tattoo Trend That Are All True Masterpieces Photo of 37 Examples of the Hypercolor Realism Tattoo Trend That Are All True Masterpieces 5000000 POPSUGAR Tatoo Floral,Floral Back Tattoos,Floral Tattoo Design,Flower Cover Up Tattoos,Colored Tattoo Design,Realistic Flower Tattoo,Best Cover Up Tattoos,Mom Tattoos,Body Art Tattoos image https://i.pinimg.com/originals/88/1c/ca/881ccad581aba0bdd081904f93402789.jpg /data/tattoos tattoos 8880 Bouvet Island (Bouvetoya) List(-84.3984, -144.933) 2018-01-25T20:23:18.000+0000 8880 Amy Brown 21 2015-11-08T16:14:16.000+0000 2018 18-24 2584 41233376-1ae4-41f7-bd0c-85959369b966 161 PCS 8 SHEETS CHRISTMAS SNOWFLAKE WINDOW CLING STICKERS FOR GLASS, 161 PCS 8 SHEETS CHRISTMAS SNOWFLAKE WINDOW CLING STICKERS FOR GLASS, 111 Starr's Crafts and Gifts Christmas Window Stickers,Christmas Window Decorations,Christmas Themes,Holiday Decor,Christmas Design,Christmas Windows,Christmas Snowflakes,Xmas,Christmas Ornaments image https://i.pinimg.com/originals/f1/93/a7/f193a7a364683324afc8eda446e56859.jpg /data/christmas christmas 2584 Cook Islands List(-87.8443, 103.624) 2019-12-19T16:09:10.000+0000 2584 Daniel Ballard 31 2015-12-04T07:01:39.000+0000 2019 25-35 250 8bf6d8fb-6f21-4d8c-86ff-3e3572875dee Beautiful Souls Healing With Art: Holly Irwin - Hello Lovely Come tour paintings and art work of celebrated Atlanta artist, Holly Irwin in Beautiful Souls Healing With Art: Holly Irwin. 115000 Hello Lovely Art Sketches,Art Drawings,Animal Drawings,Art Amour,Fine Art,Fine Fine,Beautiful Soul,Hello Beautiful,Pebble Art image https://i.pinimg.com/originals/60/25/2b/60252bca459d301010f903d0e77fd6d6.jpg /data/art art 250 France List(-84.4203, -142.539) 2018-11-08T12:14:12.000+0000 250 Cody Adams 22 2015-10-26T03:29:49.000+0000 2018 18-24 354 30d6c9ff-da42-4fe8-97ec-ebb8b147ff20 30+ Ways to Teach Art Without a Textbook Pictures are worth a thousand words - and teaching art doesn't have to be boring! Here are 30+ hands-on ways to teach art without a textbook! 21000 Learn in Color Art Lessons For Kids,Art Lessons Elementary,Art For Kids,Art Education Lessons,Preschool Art Lessons,Art Education Projects,Kids Art Class,Preschool Learning,High School Art image https://i.pinimg.com/origina

In [ ]:
# task 4 - find the most popular Pinterest category people post to based on their country.

# create count of how many times a category appears per country
task4_df = base_df.groupBy("country", "category").count().withColumnRenamed("count", "category_count")

# filter results by max category per country
country_window = Window.partitionBy("country")
task4_df = task4_df.withColumn("category_max", max("category_count").over(country_window)).where(col("category_count") == col("category_max")).drop("category_max")

display(task4_df)

country category category_count Afghanistan education 40 Albania art 60 Algeria quotes 90 American Samoa tattoos 39 Andorra tattoos 19 Angola education 8 Anguilla beauty 9 Anguilla diy-and-crafts 9 Antarctica (the territory South of 60 deg S) christmas 13 Antigua and Barbuda travel 7 Antigua and Barbuda art 7 Argentina tattoos 27 Armenia vehicles 10 Aruba christmas 23 Australia christmas 7 Austria travel 9 Austria tattoos 9 Azerbaijan finance 13 Bahamas event-planning 12 Bahrain finance 6 Bangladesh christmas 15 Barbados education 11 Belarus christmas 6 Belgium diy-and-crafts 5 Belize diy-and-crafts 10 Benin tattoos 6 Bermuda event-planning 5 Bermuda christmas 5 Bhutan diy-and-crafts 5 Bolivia home-decor 9 Bosnia and Herzegovina tattoos 9 Botswana finance 8 Bouvet Island (Bouvetoya) tattoos 8 Bouvet Island (Bouvetoya) travel 8 Brazil finance 6 Brazil home-decor 6 British Indian Ocean Territory (Chagos Archipelago) mens-fashion 4 British Virgin Islands christmas 11 Brunei Darussalam education 3 Brunei Darussalam finance 3 Brunei Darussalam event-planning 3 Brunei Darussalam diy-and-crafts 3 Brunei Darussalam home-decor 3 Bulgaria christmas 11 Burkina Faso quotes 7 Burundi mens-fashion 5 Burundi beauty 5 Cambodia beauty 5 Cameroon travel 4 Canada education 3 Canada event-planning 3 Cape Verde event-planning 2 Cape Verde quotes 2 Cape Verde diy-and-crafts 2 Cayman Islands christmas 4 Central African Republic mens-fashion 6 Chad diy-and-crafts 7 Chile mens-fashion 4 China vehicles 2 Christmas Island travel 6 Cocos (Keeling) Islands travel 4 Cocos (Keeling) Islands finance 4 Colombia home-decor 7 Comoros christmas 3 Congo education 6 Cook Islands christmas 3 Cook Islands diy-and-crafts 3 Costa Rica home-decor 6 Cote d'Ivoire beauty 3 Cote d'Ivoire christmas 3 Cote d'Ivoire event-planning 3 Cote d'Ivoire diy-and-crafts 3 Cote d'Ivoire finance 3 Croatia finance 5 Cuba diy-and-crafts 3 Cuba tattoos 3 Cyprus home-decor 3 Czech Republic travel 5 Denmark education 5 Djibouti diy-and-crafts 5 Dominica christmas 2 Dominica education 2 Dominica event-planning 2 Dominican Republic finance 6 Ecuador travel 9 Egypt vehicles 4 El Salvador travel 2 Equatorial Guinea quotes 2 Equatorial Guinea travel 2 Eritrea event-planning 3 Estonia christmas 3 Ethiopia art 5 Falkland Islands (Malvinas) christmas 4 Faroe Islands event-planning 4 Fiji education 2 Fiji quotes 2 Fiji mens-fashion 2 Finland beauty 2 Finland finance 2 Finland art 2 Finland mens-fashion 2 France diy-and-crafts 3 France beauty 3 French Guiana finance 3 French Polynesia event-planning 7 French Southern Territories finance 2 Gabon travel 3 Gambia art 2 Georgia education 3 Georgia beauty 3 Germany finance 5 Ghana quotes 3 Ghana art 3 Gibraltar beauty 2 Gibraltar mens-fashion 2 Gibraltar travel 2 Gibraltar event-planning 2 Greece mens-fashion 5 Greenland travel 2 Greenland tattoos 2 Greenland quotes 2 Grenada quotes 4 Guadeloupe christmas 5 Guam vehicles 3 Guatemala finance 3 Guatemala art 3 Guernsey tattoos 3 Guinea finance 2 Guinea travel 2 Guinea vehicles 2 Guinea-Bissau travel 5 Guyana art 2 Guyana education 2 Haiti christmas 3 Heard Island and McDonald Islands vehicles 3 Heard Island and McDonald Islands travel 3 Holy See (Vatican City State) event-planning 2 Holy See (Vatican City State) mens-fashion 2 Honduras event-planning 3 Hong Kong home-decor 2 Hungary vehicles 3 Iceland tattoos 3 India art 3 Indonesia finance 5 Iran mens-fashion 2 Iran art 2 Iran event-planning 2 Iran christmas 2 Iraq tattoos 3 Ireland christmas 1 Ireland event-planning 1 Ireland finance 1 Ireland quotes 1 Ireland diy-and-crafts 1 Ireland tattoos 1 Ireland home-decor 1 Ireland mens-fashion 1 Isle of Man art 3 Israel art 2 Italy vehicles 3 Jamaica finance 3 Japan art 3 Jersey quotes 3 Jordan diy-and-crafts 2 Kazakhstan tattoos 3 Kenya diy-and-crafts 4 Kiribati christmas 2 Kiribati finance 2 Kiribati diy-and-crafts 2 Kiribati beauty 2 Korea travel 3 Kuwait travel 3 Kuwait christmas 3 Kyrgyz Republic christmas 5

In [ ]:
# task 5 - find how many posts each category had between 2018 and 2022.

# add column with total posts per category per year
task5_df = base_df.groupBy("post_year", "category").count().withColumnRenamed("count", "category_count")

# filter by year range
task5_df = task5_df.filter(col("post_year").between(2018, 2022)).orderBy("post_year", "category")

display(task5_df)

post_year category category_count 2018 art 50 2018 beauty 59 2018 christmas 84 2018 diy-and-crafts 56 2018 education 66 2018 event-planning 52 2018 finance 58 2018 home-decor 61 2018 mens-fashion 60 2018 quotes 63 2018 tattoos 56 2018 travel 65 2018 vehicles 59 2019 art 61 2019 beauty 40 2019 christmas 69 2019 diy-and-crafts 56 2019 education 61 2019 event-planning 49 2019 finance 47 2019 home-decor 52 2019 mens-fashion 55 2019 quotes 55 2019 tattoos 59 2019 travel 50 2019 vehicles 54 2020 art 54 2020 beauty 60 2020 christmas 71 2020 diy-and-crafts 61 2020 education 51 2020 event-planning 55 2020 finance 68 2020 home-decor 48 2020 mens-fashion 63 2020 quotes 54 2020 tattoos 56 2020 travel 48 2020 vehicles 42 2021 art 60 2021 beauty 45 2021 christmas 61 2021 diy-and-crafts 56 2021 education 64 2021 event-planning 50 2021 finance 58 2021 home-decor 42 2021 mens-fashion 62 2021 quotes 64 2021 tattoos 64 2021 travel 55 2021 vehicles 48 2022 art 46 2022 beauty 46 2022 christmas 74 2022 diy-and-crafts 48 2022 education 43 2022 event-planning 42 2022 finance 53 2022 home-decor 38 2022 mens-fashion 36 2022 quotes 62 2022 tattoos 58 2022 travel 50 2022 vehicles 36

In [ ]:
# task 6 - step 1: for each country find the user with the most followers. Your query should return a DataFrame that contains the following columns: country, poster_name, follower_count

task6_df1 = base_df.select("country", "poster_name", "follower_count")

# partition by country
country_window2 = Window.partitionBy("country")

# find max follower count per country
task6_df1 = task6_df1.withColumn("follower_max", max("follower_count").over(country_window2)).where(col("follower_count") == col("follower_max"))

# select distinct combined values of country, poster_name, and follower_count
task6_df1 = task6_df1.select("country", "poster_name", "follower_count").distinct()

display(task6_df1)

country poster_name follower_count Afghanistan 9GAG 3000000 Albania The Minds Journal 5000000 Algeria Apartment Therapy 5000000 American Samoa Mamas Uncut 8000000 Andorra Teachers Pay Teachers 1000000 Angola Tastemade 8000000 Anguilla We Heart It 15000000 Antarctica (the territory South of 60 deg S) Refinery29 1000000 Antigua and Barbuda Country Living Magazine 1000000 Argentina Who What Wear 2000000 Argentina Cheezburger 2000000 Armenia Michelle {CraftyMorning.com} 892000 Aruba GQ Magazine 874000 Australia Mujer de 10 2000000 Austria Allwomenstalk - girl rules 813000 Azerbaijan Style Me Pretty 6000000 Bahamas Stylecraze 2000000 Bahrain Rainy Day Mum 337000 Bangladesh Better Homes and Gardens 4000000 Barbados The Creativity Exchange 410000 Belarus Daily Mail 2000000 Belgium This Old House 944000 Belize Julia Berolzheimer 399000 Benin Total Beauty 686000 Bermuda 3 Boys and a Dog 83000 Bhutan diana ajih 141000 Bolivia The Kitchn 1000000 Bosnia and Herzegovina Stylesatlife 388000 Botswana OkChicas 3000000 Bouvet Island (Bouvetoya) POPSUGAR 5000000 Brazil Lively 892000 British Indian Ocean Territory (Chagos Archipelago) Shopify 257000 British Virgin Islands The WHOot 1000000 Brunei Darussalam Kids Craft Room 277000 Bulgaria Half Baked Harvest 912000 Burkina Faso Behance 6000000 Burundi Studio McGee 662000 Cambodia Catch My Party 2000000 Cameroon The Blonde Abroad 123000 Canada Simply Stacie - Easy Dinner Recipes + Desserts 422000 Cape Verde The Craft Train 369000 Cayman Islands InStyle 1000000 Cayman Islands Daisy Farm Crafts 1000000 Central African Republic PureWow 868000 Chad ArchZine FR 761000 Chile TODAY Show 426000 China Empowered Sustenance 127000 Christmas Island Instructables 3000000 Cocos (Keeling) Islands How Does She 709000 Colombia DIY Magazine 466000 Comoros Ruffled 4000000 Congo Virginia | Fynes Designs : Home Decor, Easy DIY’s, Lifestyle 410000 Cook Islands Fun Loving Families: Crafts, Games, and Activities for Kids 31000 Costa Rica Martha Stewart Living 2000000 Cote d'Ivoire Mom Junction 565000 Croatia Meraki Lane 546000 Cuba Cuded Art & Design 1000000 Cyprus Redbubble 3000000 Czech Republic Tatertots and Jello .com 398000 Denmark Kelley Nan 59000 Djibouti The Dating Divas 577000 Dominica Monique - Living Life and Learning 67000 Dominican Republic My Modern Met 3000000 Ecuador LABONNI 84000 Egypt Allure 346000 El Salvador Power of Positivity 221000 Equatorial Guinea Adventure in You Travel Blog 54000 Eritrea Core77 105000 Estonia KLYKER.COM - Just Funny Pictures, No Big Deal! 27000 Ethiopia eBaumsWorld 1000000 Falkland Islands (Malvinas) A Blissful Nest 113000 Faroe Islands British Vogue 1000000 Fiji Homeschool Giveaways and Freebies 99000 Finland Buggy and Buddy 185000 France Glamour 708000 French Guiana Inkbox Tattoos 338000 French Polynesia Hunker 279000 French Southern Territories Don't Waste the Crumbs 119000 Gabon One Crazy Mom 175000 Gambia The Travel Hacking Life 61000 Georgia Susie Allison | Busy Toddler 203000 Germany Azuro Republic 122000 Ghana Zina Harrington 1000000 Gibraltar Top Inspired 855000 Greece Thirty Handmade Days 397000 Greenland The Educators' Spin On It 2000000 Grenada Michael Bliss 459000 Guadeloupe Kathy+Steve | TBD + TGG + OhMeOhMy 355000 Guam imgur 4000000 Guatemala Homedit.com 965000 Guernsey Y Travel Blog 4000000 Guinea Cars Zone 134000 Guinea-Bissau Kristina Buskirk | Toddler Approved 160000 Guyana Liska @ Adventure in a Box 49000 Haiti No Time For Flash Cards 610000 Heard Island and McDonald Islands Real Men Real Style 487000 Holy See (Vatican City State) Viva Decora 2000000 Honduras Mad in Crafts 106000 Hong Kong Remodelista 991000 Hungary TheFunnyBeaver.Com 814000 Iceland PositiveMed 371000 India Rosie's Sketchbook 235000 Indonesia Forbes 252000 Iran WeddingWire 520000 Iraq House Beautiful 876000 Ireland Deavita.fr 239000 Isle of Man Quinceanera.com 195000 Israel On Point Fresh 44000 Italy BeSpotted 46000 Jamaica Eating Bird Food 397000 Japan Beautiful Dawn | Arts & Crafts · Croch

In [ ]:
# task 6 - step 2: based on the above query, find the country with the user with most followers.

task6_df2 = task6_df1.select("country", "follower_count").orderBy("follower_count", ascending=False).limit(1)

display(task6_df2)

country follower_count Anguilla 15000000

In [ ]:
# task 7 - what is the most popular category people post to based on the following age groups: 18-24, 25-35, 36-50, +50

task7_df = base_df.groupBy("age_group", "category").count().withColumnRenamed("count", "category_count")

agegroup_window = Window.partitionBy("age_group")

task7_df = task7_df.withColumn("category_max", max("category_count").over(agegroup_window)).where(col("category_count") == col("category_max")).drop("category_max")

display(task7_df)

age_group category category_count 18-24 tattoos 198 25-35 christmas 131 36-50 christmas 75 36-50 finance 75 50+ mens-fashion 37

In [ ]:
# task 8 - what is the median follower count for users in the following age groups: 18-24, 25-35, 36-50, +50

task8_df = base_df

# median followers per age_group
task8_df = task8_df.groupBy("age_group").agg(expr("percentile_approx(follower_count, 0.5)").alias("median_follower_count")).orderBy("age_group")

display(task8_df)

age_group median_follower_count 18-24 136000 25-35 21000 36-50 7000 50+ 3000

In [ ]:
# task 9 - find how many users have joined between 2015 and 2020.

task9_df = user_df.withColumn("post_year", year("date_joined")).drop("ind").dropDuplicates()
task9_df = task9_df.groupBy("post_year").agg(count(year("date_joined")).alias("number_users_joined")).filter(col("post_year").between(2015,2020))

display(task9_df)

post_year number_users_joined 2015 471 2016 1217 2017 590

In [ ]:
# task 10 - find the median follower count of users have joined between 2015 and 2020.
# Your query should return a DataFrame that contains the following columns: post_year, a new column that contains only the year from the timestamp column & median_follower_count, a new column containing the desired query output

task10_df = base_df.select("user_name", "poster_name", "age", "date_joined", "follower_count").withColumn("post_year", year("date_joined")).filter(col("post_year").between(2015,2020)).dropDuplicates()

task10_df = task10_df.groupBy("post_year").agg(expr("percentile_approx(follower_count, 0.5)").alias("median_follower_count"))

display(task10_df)

post_year median_follower_count 2015 40000 2016 13000 2017 3000

In [ ]:
# task 11 - find the median follower count of users that have joined between 2015 and 2020, based on which age group they are part of.

task11_df = base_df.select("user_name", "poster_name", "age_group", "date_joined", "follower_count").withColumn("post_year", year("date_joined")).filter(col("post_year").between(2015,2020)).dropDuplicates()

task11_df = task11_df.groupBy("post_year", "age_group").agg(expr("percentile_approx(follower_count, 0.5)").alias("median_follower_count")).orderBy("post_year", "age_group", ascending=True)

display(task11_df)

post_year age_group median_follower_count 2015 18-24 98000 2015 25-35 28000 2015 36-50 8000 2015 50+ 17000 2016 18-24 31000 2016 25-35 17000 2016 36-50 8000 2016 50+ 2000 2017 18-24 7000 2017 25-35 4000 2017 36-50 3000 2017 50+ 2000